This notebook runs a `Qallse` model in simulation mode and shows how to simply visualize the results using utilities defined in module `hepqpr.qallse.plotting`.

# Import and setup

In [1]:
# import modules
import pandas as pd
import numpy as np
from hepqpr.qallse.plotting import *
from hepqpr.qallse import *
from hepqpr.qallse.dsmaker import create_dataset

# initialise the plotting module in "notebook" mode
set_notebook_mode()

# initialise the logging module
import logging
logging.basicConfig()
fmt = logging.Formatter("%(asctime)s.%(msecs)03d %(levelname)s %(name)s: %(message)s", datefmt='%H:%M:%S')
for handler in logging.getLogger().handlers: handler.setFormatter(fmt)
logging.getLogger('hepqpr').setLevel(logging.DEBUG)

0
1
2
3
[(-inf, inf)]
[(0.0, 0.6)]
[(0.0, 0.6), (0.5, 1.1)]
[(0.0, 0.6), (0.5, 1.1), (1.0, 1.6)]
[(0.0, 0.6), (0.5, 1.1), (1.0, 1.6), (1.5, 2.1)]


# Define run config

In [2]:
# == DATASET CONFIG

dsmaker_config = dict(
    density=.1, # 1% 
)
#    density=.10, # 1% 

# == INPUT CONFIG

# whether or not to add missing doublets to the input
add_missing = True 

# == RUN CONFIG

model_class = Qallse # model class to use
extra_config = dict() # configuration arguments overriding the defaults

# Generate the data

In [3]:
import tempfile

tempdir = tempfile.TemporaryDirectory()
print(f'using {tempdir.name}')
#random_seed=240834366
metas, path = create_dataset(output_path=tempdir.name, gen_doublets=True, random_seed=240834351, **dsmaker_config)

using /var/folders/7r/y3xzyywn4mg2tfhg0sgjqx_w0000gn/T/tmpeeg64xr1


00:51:31.817 DEBUG hepqpr.qallse.dsmaker.dsmaker: Loaded 120939 hits from /Users/parkerreid/hepqpr-qallse/src/hepqpr/qallse/dsmaker/data/event000001000.
00:51:31.847 DEBUG hepqpr.qallse.dsmaker.dsmaker: Filtered hits from barrel. Remaining hits: 65518.
00:51:31.898 DEBUG hepqpr.qallse.dsmaker.dsmaker: Dropped double hits. Remaining hits: 55446.
00:51:31.948 DEBUG hepqpr.qallse.dsmaker.dsmaker: High Pt hits: 32302/5484
00:51:32.156 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_hits=5484
00:51:32.157 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_tracks=818
00:51:32.158 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_important_tracks=60
00:51:32.159 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_noise=1303
00:51:32.160 DEBUG hepqpr.qallse.dsmaker.dsmaker:   random_seed=240834351
00:51:32.161 DEBUG hepqpr.qallse.dsmaker.dsmaker:   time=2020-03-31T00:51:32.156896
00:51:35.312 INFO hepqpr.qallse.dsmaker.dsmaker: Doublets (len=100811) generated in f/var/folders/7r/y3xzyywn4mg2tfhg0sgjqx_w0000gn/T/tmpeeg64xr

In [4]:
with open(path + '-meta.json') as f:
    print(f.read())

{
    "num_hits": 5484,
    "num_tracks": 818,
    "num_important_tracks": 60,
    "num_noise": 1303,
    "random_seed": 240834351,
    "time": "2020-03-31T00:51:32.156896",
    "params": {
        "input_path": "/Users/parkerreid/hepqpr-qallse/src/hepqpr/qallse/dsmaker/data/event000001000",
        "output_path": "/var/folders/7r/y3xzyywn4mg2tfhg0sgjqx_w0000gn/T/tmpeeg64xr1",
        "density": 0.1,
        "high_pt_cut": 1.0,
        "double_hits_ok": false,
        "gen_doublets": true,
        "prefix": null,
        "random_seed": 240834351,
        "phi_bounds": null,
        "min_hits_per_track": 5
    }
}


# Execute the model

## Load the data

In [5]:
# load data
dw = DataWrapper.from_path(path)
doublets = pd.read_csv(path + '-doublets.csv')
if add_missing:
    doublets = dw.add_missing_doublets(doublets)
else:
    p, r, ms = dw.compute_score(doublets)
    print(f'got {len(doublets)}.')
    print(f'  Input precision (%): {p*100:.4f}, recall (%): {r*100:.4f}, missing: {len(ms)}')

got 100811 doublets.
  Input precision (%): 0.4427, recall (%): 98.1982
    New precision (%): 0.4508


## Build the model

In [6]:
%%time

# instantiate qallse
model = model_class(dw, **extra_config)
# build the qubo
model.build_model(doublets=doublets)
sliceContainer = model.to_qubo()
print(data_structures.Volayer.phi_increment)
print(data_structures.Volayer.eta_slices)
print(data_structures.Volayer.phi_slices)

00:51:37.163 DEBUG hepqpr.qallse.qallse: using config:
00:51:37.164 DEBUG hepqpr.qallse.qallse:     cheat: False
00:51:37.165 DEBUG hepqpr.qallse.qallse:     max_layer_span: 2
00:51:37.166 DEBUG hepqpr.qallse.qallse:     num_multiplier: -1
00:51:37.167 DEBUG hepqpr.qallse.qallse:     qplet_max_dcurv: 0.0001
00:51:37.167 DEBUG hepqpr.qallse.qallse:     qplet_max_strength: -0.2
00:51:37.168 DEBUG hepqpr.qallse.qallse:     qubo_bias_weight: 0
00:51:37.168 DEBUG hepqpr.qallse.qallse:     qubo_conflict_strength: 1
00:51:37.169 DEBUG hepqpr.qallse.qallse:     rz_power: 1
00:51:37.170 DEBUG hepqpr.qallse.qallse:     strength_bounds: None
00:51:37.170 DEBUG hepqpr.qallse.qallse:     tplet_max_curv: 0.0008
00:51:37.172 DEBUG hepqpr.qallse.qallse:     tplet_max_drz: 0.1
00:51:37.175 DEBUG hepqpr.qallse.qallse:     volayer_power: 2
00:51:37.176 DEBUG hepqpr.qallse.qallse:     xy_power: 1
00:51:37.177 DEBUG hepqpr.qallse.qallse:     xy_relative_strength: 0.5
00:51:39.596 INFO hepqpr.qallse.qallse:

0.5
[(-inf, inf)]
[(0.0, 0.6), (0.5, 1.1), (1.0, 1.6), (1.5, 2.1)]
CPU times: user 14 s, sys: 165 ms, total: 14.1 s
Wall time: 14.3 s


## Sample the QUBO

Here, we use [_qbsolv_](https://github.com/dwavesystems/qbsolv) with default arguments. This means only classical algorithms.

In [7]:
%%time
# execute the qubo
responseContainer = model.sample_qubo_slices(Q=sliceContainer)
#response = model.sample_qubo_slices(Q=qslice)

{('35798_41814_73903', '35798_41814_73903'): 0, ('23539_38970_45738', '23539_38970_45738'): 0, ('23539_31462_38970', '23539_31462_38970'): 0, ('23539_31462_45738', '23539_31462_45738'): 0, ('35827_73913_81013', '35827_73913_81013'): 0, ('35827_42417_73913', '35827_42417_73913'): 0, ('35827_42417_81013', '35827_42417_81013'): 0, ('23600_31499_45756', '23600_31499_45756'): 0, ('23600_31499_38991', '23600_31499_38991'): 0, ('27199_33899_40017', '27199_33899_40017'): 0, ('27196_33899_40017', '27196_33899_40017'): 0, ('27196_40017_71831', '27196_40017_71831'): 0, ('27199_40017_71831', '27199_40017_71831'): 0, ('82945_96069_112089', '82945_96069_112089'): 0, ('19444_28550_41852', '19444_28550_41852'): 0, ('82950_89717_96075', '82950_89717_96075'): 0, ('82945_89711_96069', '82945_89711_96069'): 0, ('19454_27740_35194', '19454_27740_35194'): 0, ('19444_28550_35858', '19444_28550_35858'): 0, ('19444_35858_41852', '19444_35858_41852'): 0, ('19454_27740_41397', '19454_27740_41397'): 0, ('40017_71

00:51:52.423 INFO hepqpr.qallse.qallse: QUBO of size 2162 sampled in 0.95s (seed 523592239).
00:51:53.672 INFO hepqpr.qallse.qallse: QUBO of size 1684 sampled in 2.19s (seed 523592239).


{('42552_74644_81600', '42552_74644_81600'): 0, ('42552_81600_88248', '42552_81600_88248'): 0, ('20333_28092_35470', '20333_28092_35470'): 0, ('20333_35457_41592', '20333_35457_41592'): 0, ('20333_28093_41592', '20333_28093_41592'): 0, ('20333_28093_35457', '20333_28093_35457'): 0, ('20333_35470_41595', '20333_35470_41595'): 0, ('41573_73195_79986', '41573_73195_79986'): 0, ('41543_73568_86744', '41543_73568_86744'): 0, ('41543_73568_80290', '41543_73568_80290'): 0, ('41577_73619_80321', '41577_73619_80321'): 0, ('41543_80290_86744', '41543_80290_86744'): 0, ('41577_73619_86782', '41577_73619_86782'): 0, ('42611_74075_81158', '42611_74075_81158'): 0, ('42611_74075_87439', '42611_74075_87439'): 0, ('41577_80321_86782', '41577_80321_86782'): 0, ('42611_81158_87439', '42611_81158_87439'): 0, ('42653_74132_81192', '42653_74132_81192'): 0, ('42653_81192_87875', '42653_81192_87875'): 0, ('42653_74132_87875', '42653_74132_87875'): 0, ('20347_28092_41595', '20347_28092_41595'): 0, ('20347_2809

00:51:55.686 INFO hepqpr.qallse.qallse: QUBO of size 3298 sampled in 4.19s (seed 523592239).


{('23383_31419_45071', '23383_31419_45071'): 0, ('23383_31419_38509', '23383_31419_38509'): 0, ('23383_38509_45071', '23383_38509_45071'): 0, ('23539_38970_45738', '23539_38970_45738'): 0, ('23539_31462_38970', '23539_31462_38970'): 0, ('23539_31462_45738', '23539_31462_45738'): 0, ('29299_36416_42864', '29299_36416_42864'): 0, ('29299_36416_74290', '29299_36416_74290'): 0, ('39248_45666_77412', '39248_45666_77412'): 0, ('39248_45666_84648', '39248_45666_84648'): 0, ('39248_77412_84648', '39248_77412_84648'): 0, ('82388_88863_95092', '82388_88863_95092'): 0, ('82392_88863_95092', '82392_88863_95092'): 0, ('82361_88833_95080', '82361_88833_95080'): 0, ('82745_89543_95669', '82745_89543_95669'): 0, ('39285_77717_85099', '39285_77717_85099'): 0, ('45688_77164_84677', '45688_77164_84677'): 0, ('45666_77412_84648', '45666_77412_84648'): 0, ('45738_77213_84713', '45738_77213_84713'): 0, ('44070_75502_82745', '44070_75502_82745'): 0, ('44070_75502_89543', '44070_75502_89543'): 0, ('44070_8274

00:51:57.170 INFO hepqpr.qallse.qallse: QUBO of size 2281 sampled in 5.67s (seed 523592239).


CPU times: user 5.61 s, sys: 55.1 ms, total: 5.67 s
Wall time: 5.71 s


## Parse the results

In [8]:
# get all output doublets
all_doublets = model.process_sample_slices(responseContainer=responseContainer)
# recreate tracks and resolve remaining conflicts
final_tracks, final_doublets = TrackRecreaterD().process_results(all_doublets)

00:51:57.193 INFO hepqpr.qallse.track_recreater: Found 54 conflicting doublets
00:51:57.196 DEBUG hepqpr.qallse.track_recreater: Conflicts added: [82945, 89711], [37263, 75502], [74272, 87581], [82233, 95012], [22997, 37874], [37751, 76345], [75727, 82950], [109056, 114062], [80832, 87569], [29635, 44201], [35427, 73195], [28031, 35427], [36025, 74639], [28775, 36025], [43176, 74582], [74582, 88637], [43919, 75849], [75849, 89808], [21855, 37541], [29276, 42202], [20709, 29276].
00:51:57.196 INFO hepqpr.qallse.track_recreater: Added 21 conflicting doublets


-8.0


# Evaluate the results

## Print statistics and scores

In [9]:
# stats about the qbsolv run
#en0 = dw.compute_energy(Q)
#en = response.record.energy[0]

#print(f'SAMPLE -- energy: {en:.4f}, ideal: {en0:.4f} (diff: {en-en0:.6f})')
#occs = response.record.num_occurrences
#print(f'          best sample occurrence: {occs[0]}/{occs.sum()}')

# scores
p, r, missings = dw.compute_score(final_doublets)
print(f'SCORE  -- precision (%): {p * 100}, recall (%): {r * 100}, missing: {len(missings)}')
trackml_score = dw.compute_trackml_score(final_tracks)
print(f'          tracks found: {len(final_tracks)}, trackml score (%): {trackml_score * 100}')

SCORE  -- precision (%): 94.89559164733178, recall (%): 92.11711711711712, missing: 35
          tracks found: 103, trackml score (%): 86.63302722459801


### Plot the results

You have the following at your disposal:
```python
iplot_results(dw, final_doublets, missings, dims=list('xy'))
iplot_results_tracks(dw, final_doublets, missings, dims=list('zr'))
iplot_results_any(dw, dw.real_doublets, dims=list('xy'))
```

For 3D plots, simply define `dims` as 3-dimensional. For example:
```python
iplot_results(dw, final_doublets, missings, dims=list('zxy'))
```

In [10]:
iplot_results(dw,final_doublets,missings, dims=list('xy'))

In [11]:
iplot_results(dw, final_doublets, missings, dims=list('zr'))

In [12]:
#iplot_results(dw, final_doublets, missings, dims=list('zxy'))

In [13]:
iplot_results(dw, final_doublets, missings, dims=list('zy'))

In [14]:
print(data_structures.Volayer.phi_increment)
data_structures.Volayer.eta_increment = 0.2
data_structures.Volayer.phi_increment = 2.0
print(data_structures.Volayer.phi_increment)

0.5
2.0


In [15]:
dw1 = DataWrapper.from_path(path)
doublets = pd.read_csv(path + '-doublets.csv')
if add_missing:
    doublets = dw1.add_missing_doublets(doublets)
else:
    p, r, ms = dw.compute_score(doublets)
    print(f'got {len(doublets)}.')
    print(f'  Input precision (%): {p*100:.4f}, recall (%): {r*100:.4f}, missing: {len(ms)}')

got 100811 doublets.
  Input precision (%): 0.4427, recall (%): 98.1982
    New precision (%): 0.4508


In [16]:
data_structures.Volayer.phi_slices = [(0.0, 2.0)]
model1 = model_class(dw, **extra_config)
print(data_structures.Volayer.phi_increment)
data_structures.Volayer.eta_increment = 0.2
data_structures.Volayer.phi_increment = 2.0
print(data_structures.Volayer.phi_increment)
# build the qubo
data_structures.Volayer.phi_slices = [(0.0, 2.0)]
model1.build_model(doublets=doublets)
data_structures.Volayer.phi_slices = [(0.0, 2.0)]
sliceContainer1 = model1.to_qubo()

00:52:18.618 DEBUG hepqpr.qallse.qallse: using config:
00:52:18.619 DEBUG hepqpr.qallse.qallse:     cheat: False
00:52:18.620 DEBUG hepqpr.qallse.qallse:     max_layer_span: 2
00:52:18.620 DEBUG hepqpr.qallse.qallse:     num_multiplier: -1
00:52:18.621 DEBUG hepqpr.qallse.qallse:     qplet_max_dcurv: 0.0001
00:52:18.622 DEBUG hepqpr.qallse.qallse:     qplet_max_strength: -0.2
00:52:18.622 DEBUG hepqpr.qallse.qallse:     qubo_bias_weight: 0
00:52:18.623 DEBUG hepqpr.qallse.qallse:     qubo_conflict_strength: 1
00:52:18.623 DEBUG hepqpr.qallse.qallse:     rz_power: 1
00:52:18.624 DEBUG hepqpr.qallse.qallse:     strength_bounds: None
00:52:18.625 DEBUG hepqpr.qallse.qallse:     tplet_max_curv: 0.0008
00:52:18.625 DEBUG hepqpr.qallse.qallse:     tplet_max_drz: 0.1
00:52:18.626 DEBUG hepqpr.qallse.qallse:     volayer_power: 2
00:52:18.627 DEBUG hepqpr.qallse.qallse:     xy_power: 1
00:52:18.627 DEBUG hepqpr.qallse.qallse:     xy_relative_strength: 0.5


2.0
2.0


00:52:20.995 INFO hepqpr.qallse.qallse: created 50809 doublets.
00:52:32.172 INFO hepqpr.qallse.qallse: created 14295 triplets.
00:52:32.344 INFO hepqpr.qallse.qallse: created 1535 quadruplets.
00:52:32.345 INFO hepqpr.qallse.qallse: Model built in 12.88s. doublets: 50809/1374, triplets: 14295/1561, quadruplets: 1535
00:52:32.348 INFO hepqpr.qallse.qallse: Dropped 8 real structures during preprocessing
00:52:32.352 DEBUG hepqpr.qallse.qallse: 
    type                      hid    reason      arg1  arg2
0  tplet        19988_28861_36080      curv -0.008034   NaN
1  tplet        28861_36080_42582      curv -0.003800   NaN
2  tplet        36080_42582_74065      curv  0.002523   NaN
3  tplet        42582_74065_81133      curv -0.002005   NaN
4  tplet        74065_81133_88679      curv  0.002147   NaN
5  tplet        81133_88679_95572      curv  0.000913   NaN
6  tplet       88679_95572_112552      curv  0.002149   NaN
7  qplet  18978_27522_34094_71942  strength -0.183443   NaN
00:52:32.354

In [17]:
# execute the qubo
responseContainer1 = model1.sample_qubo_slices(Q=sliceContainer1)
#response = model.sample_qubo_slices(Q=qslice)

{('41663_73720_80416', '41663_73720_80416'): 0, ('41663_73720_86532', '41663_73720_86532'): 0, ('41663_80416_86532', '41663_80416_86532'): 0, ('23025_31290_38868', '23025_31290_38868'): 0, ('42799_81287_87550', '42799_81287_87550'): 0, ('41698_73324_86566', '41698_73324_86566'): 0, ('20867_31282_45976', '20867_31282_45976'): 0, ('41698_73324_80072', '41698_73324_80072'): 0, ('19584_34696_40629', '19584_34696_40629'): 0, ('41698_80072_86566', '41698_80072_86566'): 0, ('20870_28291_41698', '20870_28291_41698'): 0, ('42824_74272_87569', '42824_74272_87569'): 0, ('42824_74278_80832', '42824_74278_80832'): 0, ('21178_29485_42944', '21178_29485_42944'): 0, ('42864_81339_88003', '42864_81339_88003'): 0, ('21178_29485_36541', '21178_29485_36541'): 0, ('42864_74290_88003', '42864_74290_88003'): 0, ('42864_74290_81339', '42864_74290_81339'): 0, ('18679_27311_40066', '18679_27311_40066'): 0, ('41720_73359_80107', '41720_73359_80107'): 0, ('21178_36541_42944', '21178_36541_42944'): 0, ('19545_2775

00:52:37.579 INFO hepqpr.qallse.qallse: QUBO of size 7829 sampled in 5.13s (seed 1576152735).


In [18]:
# get all output doublets
all_doublets1 = model1.process_sample_slices(responseContainer=responseContainer1)
# recreate tracks and resolve remaining conflicts
final_tracks1, final_doublets1 = TrackRecreaterD().process_results(all_doublets1)

00:52:37.597 INFO hepqpr.qallse.track_recreater: Found 0 conflicting doublets


In [19]:
# scores
p, r, missings = dw1.compute_score(final_doublets1)
print(f'SCORE  -- precision (%): {p * 100}, recall (%): {r * 100}, missing: {len(missings)}')
trackml_score = dw1.compute_trackml_score(final_tracks1)
print(f'          tracks found: {len(final_tracks1)}, trackml score (%): {trackml_score * 100}')

SCORE  -- precision (%): 97.51693002257336, recall (%): 97.2972972972973, missing: 12
          tracks found: 100, trackml score (%): 97.18526898390549


In [20]:
iplot_results(dw1,final_doublets1, missings, dims=list('xy'))

In [21]:
new_doublets = []
for doublet in final_doublets:
    if doublet not in final_doublets1:
        new_doublets.append(doublet)

In [22]:
print(new_doublets)

[[19104, 27606], [19811, 28752], [28752, 36022], [37263, 75502], [74272, 87581], [22997, 37874], [37751, 76345], [29635, 44201], [35427, 73195], [36025, 74639], [74582, 88637], [75849, 89808], [29276, 42202]]


In [23]:
iplot_results(dw,new_doublets, missings, dims=list('xy'))

In [24]:
iplot_results(dw1,new_doublets, missings, dims=list('zr'))